<a href="https://colab.research.google.com/github/kstrickland680/MentalHealthRedditAnalysis/blob/main/DataGathering.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import requests
import pandas as pd
import json
import csv
import time
import datetime

In [ ]:

import sys
sys.path.append('/content/drive/MyDrive/MentalHealthReddit/')
import config

# Data Gathering
This notebook is dedicated to gathering data from Reddit to be used for analysis. I use the Pushshift API which is used when analyzing large amounts of Reddit data.  

## Helper Functions

In this section, I define helper functions to gather information from Reddit.  I use the pushshift api. Pushshift is a big-data storage project that contains a copy of reddit comments and submissions.  It is more useful than the reddit API alone wen analyzing large quantities of data.  

I define a basic function to get the data (getPushshiftData).  Data queries are limited to 100 returned at a time, so I also create getAllPushshiftData to gather more data than 100 for a search. 

CollectData, collectCommentData, and collectOtherSubmissionData gather the relevant information from the searches and store it as a dictionary entry. 

In [ ]:
def getPushshiftData(query, before, sub, sz):
  """
  Returns Reddit Data for the query term in the specified subreddit. 
    Paramaters: 
      query - string: what to search
      before - int: UTC date to gather data before
      sub - string: subreddit to gather data from
      sz - int: number of results  
    Returns:
      Reddit data 
  """
  url = 'https://api.pushshift.io/reddit/search/submission/?title='+str(query)+'&limit='+str(sz)+'&before='+str(before)+'&subreddit='+str(sub)

  print(url)
  r = requests.get(url)
  data = json.loads(r.text)
  return data['data']


In [ ]:
def collectData(submission, stats, bpd=False, bipolar=False):
  """
  Collects submission data. 
    Paramaters: 
      submission: the reddit data
      stats: dictionary you want the information added to
      bpd: Whether the data is from the bpd subreddit
      bipolar: Whether the data is from the bipolar reddit
  Appends the gathered information into the dictionary, with the author as key 
  """
  #submission and a dictionary you want it appnded too 
  subData = list() #list to store data points
  title = submission['title']
  url = submission['url']
  try:
      flair = submission['link_flair_text']
  except KeyError:
      flair = "NaN"    
  author = submission['author']
  sub_id = submission['id']
  score = submission['score']
  created = datetime.datetime.fromtimestamp(submission['created_utc']) #1520561700.0
  created_utc = submission['created_utc']
  numComms = submission['num_comments']
  permalink = submission['permalink']
  try:
    selftext = submission['selftext']
  except KeyError:
    selftext = "NaN"
  subreddit = submission['subreddit']
  #author_id = submission['author_fullname']
  if bpd:
    if flair == 'Person w/o BPD':
      return
  if bipolar:
    if ((flair == 'Undiagnosed') or (flair == 'Friend/Family')):
      return

  subData = [sub_id,title,url,score,created,created_utc,numComms,permalink,flair,selftext,subreddit]
  stats[author] = subData

In [ ]:
def collectCommentData(submission, stats):
  """
  Collects comment data and adds it to the dictionary. 
  Parameters:
    Submission: Data from redit
    Stats: Dictionary to add the information to. 
  Appends the gathered information into the dictionary, with the comment_ID as key
  """

  #submission and a dictionary you want it appnded too 
  subData = list() #list to store data points
  author = submission['author']
  com_id = submission['id']
  score = submission['score']
  created = datetime.datetime.fromtimestamp(submission['created_utc']) #1520561700.0
  created_utc = submission['created_utc']
  body = submission['body']
  try:
    url = submission['permalink']
  except KeyError:
    url = "NaN"
  subreddit = submission['subreddit']
  #author_id = submission['author_fullname']
 

  subData = [author,score,created,created_utc,url,body,subreddit]
  stats[com_id] = subData

In [ ]:
def collectOtherSubmissionData(submission, stats):
  """
  Collects submission data and adds it to the dictionary. 
  *Different from collectData in the key it uses to add the information to the dictionary*  
  Parameters:
    Submission: Data from redit
    Stats: Dictionary to add the information to. 
  Appends the gathered information into the dictionary, with the sub_ID as key
  """
  #submission and a dictionary you want it appnded too 
  subData = list() #list to store data points
  title = submission['title']
  url = submission['url']
  try:
      flair = submission['link_flair_text']
  except KeyError:
      flair = "NaN"    
  author = submission['author']
  sub_id = submission['id']
  score = submission['score']
  created = datetime.datetime.fromtimestamp(submission['created_utc']) #1520561700.0
  created_utc = submission['created_utc']
  numComms = submission['num_comments']
  permalink = submission['permalink']
  try:
    selftext = submission['selftext']
  except KeyError:
    selftext = "NaN"
  subreddit = submission['subreddit']
  #author_id = submission['author_fullname']

  subData = [author, title,url,score,created,created_utc,numComms,permalink,flair,selftext,subreddit]
  stats[sub_id] = subData

In [ ]:
def getAllPushshiftData(query, before, sub, size):
    """
  Returns Reddit Data for the query term in the specified subreddit.
  *Different from Pushshift Data in that it runs more than one pushshift search*  
    Paramaters: 
      query - string: what to search
      before - int: UTC date to gather data before
      sub - string: subreddit to gather data from
      sz - int: number of results  
    Returns:
      Reddit data 
  """
  returndata = getPushshiftData(query, before, sub, size)
  #print(type(returndata))
  length = len(returndata)
  newdata = [1]
  while (length < size) and (len(newdata) !=0): 
    newdata = getPushshiftData(query, returndata[-1]['created_utc'], sub, size)
    returndata = returndata + newdata
    length = len(returndata)
    print(len(returndata))
    time.sleep(1)
  return returndata



## Gathering users for the "experimetal" classes. 

In this section, I go through and identify the users whose posts and comments I'll be examining for the "experimental" classes. 

### Borderline Personality Data 

I gather entries to be classified as borderlne personality disorder. Users are classified as belonging to this class if their flair doesn't mark them as a friend/family member or undiagnosed. I store the post that identifies them for the dataset.  1417 users were identified for this class. 

In [ ]:

bpd_dict = {}
bpddata = getAllPushshiftData("", 1612069200, 'bpd', 2000)

for submission in bpddata:
  collectData(submission, bpd_dict, bpd=True)

print(str(len(bpd_dict)) + " submissions have added to list")


https://api.pushshift.io/reddit/search/submission/?title=&limit=2000&before=1612069200&subreddit=bpd
https://api.pushshift.io/reddit/search/submission/?title=&limit=2000&before=1612026749&subreddit=bpd
200
https://api.pushshift.io/reddit/search/submission/?title=&limit=2000&before=1611970771&subreddit=bpd
300
https://api.pushshift.io/reddit/search/submission/?title=&limit=2000&before=1611911462&subreddit=bpd
400
https://api.pushshift.io/reddit/search/submission/?title=&limit=2000&before=1611868930&subreddit=bpd
500
https://api.pushshift.io/reddit/search/submission/?title=&limit=2000&before=1611809256&subreddit=bpd
600
https://api.pushshift.io/reddit/search/submission/?title=&limit=2000&before=1611675630&subreddit=bpd
700
https://api.pushshift.io/reddit/search/submission/?title=&limit=2000&before=1611624200&subreddit=bpd
800
https://api.pushshift.io/reddit/search/submission/?title=&limit=2000&before=1611586873&subreddit=bpd
900
https://api.pushshift.io/reddit/search/submission/?title=&l

### Depression
I gather entries to be classified as depressed. Users are classified as belonging to this class if they self-report themselves as diagnosed in a post in the subreddit depression. I store the post that identifies them for the dataset. 1009 users were identified for this class.

In [ ]:
dep_search = ['"I was diagnosed with depression"', '"My depression"', '"I was diagnosed with MDD"', 
              '"I am diagnosed with depression"']

dep_dict = {}
depdata = []

for item in dep_search:
  depdata2 = getAllPushshiftData(item, 1612069200, 'depression', 1000)
  type(depdata2)
  depdata = depdata+depdata2

for submission in depdata:
  collectData(submission, dep_dict)

print(str(len(dep_dict)) + " submissions have added to list")



https://api.pushshift.io/reddit/search/submission/?title="I was diagnosed with depression"&limit=1000&before=1612069200&subreddit=depression
https://api.pushshift.io/reddit/search/submission/?title="I was diagnosed with depression"&limit=1000&before=1299378808&subreddit=depression
66
https://api.pushshift.io/reddit/search/submission/?title="My depression"&limit=1000&before=1612069200&subreddit=depression
https://api.pushshift.io/reddit/search/submission/?title="My depression"&limit=1000&before=1610807469&subreddit=depression
200
https://api.pushshift.io/reddit/search/submission/?title="My depression"&limit=1000&before=1609506482&subreddit=depression
300
https://api.pushshift.io/reddit/search/submission/?title="My depression"&limit=1000&before=1607980399&subreddit=depression
400
https://api.pushshift.io/reddit/search/submission/?title="My depression"&limit=1000&before=1606382235&subreddit=depression
500
https://api.pushshift.io/reddit/search/submission/?title="My depression"&limit=1000&

In [ ]:
dep_dict

{'Funny_Eyebrow': ['k3yk8o',
  'After breakup, I feel completely numb, is this normal? I was diagnosed with depression 3 years ago.',
  'https://www.reddit.com/r/depression/comments/k3yk8o/after_breakup_i_feel_completely_numb_is_this/',
  1,
  datetime.datetime(2020, 11, 30, 16, 0, 33),
  1606752033,
  0,
  '/r/depression/comments/k3yk8o/after_breakup_i_feel_completely_numb_is_this/',
  'NaN',
  '[removed]',
  'depression'],
 'leafy_and_lethal': ['j950tb',
  'Friday I was diagnosed with depression and today is my first day on meds',
  'https://www.reddit.com/r/depression/comments/j950tb/friday_i_was_diagnosed_with_depression_and_today/',
  1,
  datetime.datetime(2020, 10, 11, 13, 1, 39),
  1602421299,
  0,
  '/r/depression/comments/j950tb/friday_i_was_diagnosed_with_depression_and_today/',
  'NaN',
  "Hello everyone? I'm new here! \n\nThe person who gave me the diagnosis said on the outside I'm super bubbly. Then barely under the surface I am a sad person. I am sad. I felt that I wasn'

### Bipolar

I gather entries to be classified as bipolar. Users are classified as belonging to this class if their flair doesn't mark them as a friend/family member or undiagnosed when they posted in the subreddit "BipolarReddit". I store the post that identifies them for the dataset.  1572 users were identified for this class. 

In [ ]:
bipolar_dict = {}

bipolardata = getAllPushshiftData("", 1612069200, 'BipolarReddit', 3000)


for submission in bipolardata:
  collectData(submission, bipolar_dict, bipolar=True)

print(str(len(bipolar_dict)) + " submissions have added to list")


https://api.pushshift.io/reddit/search/submission/?title=&limit=3000&before=1612069200&subreddit=BipolarReddit
https://api.pushshift.io/reddit/search/submission/?title=&limit=3000&before=1611806251&subreddit=BipolarReddit
200
https://api.pushshift.io/reddit/search/submission/?title=&limit=3000&before=1611480420&subreddit=BipolarReddit
300
https://api.pushshift.io/reddit/search/submission/?title=&limit=3000&before=1611275350&subreddit=BipolarReddit
400
https://api.pushshift.io/reddit/search/submission/?title=&limit=3000&before=1611022458&subreddit=BipolarReddit
500
https://api.pushshift.io/reddit/search/submission/?title=&limit=3000&before=1610783624&subreddit=BipolarReddit
600
https://api.pushshift.io/reddit/search/submission/?title=&limit=3000&before=1610531078&subreddit=BipolarReddit
700
https://api.pushshift.io/reddit/search/submission/?title=&limit=3000&before=1610339886&subreddit=BipolarReddit
800
https://api.pushshift.io/reddit/search/submission/?title=&limit=3000&before=16101100

### PTSD

I gather entries to be classified as PTSD. Users are classified as belonging to this class if they self-report themselves as diagnosed in a post in the subreddit "ptsd". I store the post that identifies them for the dataset. 1090 users were identified for this class.

In [ ]:
ptsd_search = ['"I was diagnosed with PTSD"', '"My PTSD"', '"I am diagnosed with PTSD"', '"I have PTSD"']

ptsd_dict = {}
ptsddata = []

for item in ptsd_search:
  ptsddata2 = getAllPushshiftData(item, 1612069200, 'ptsd', 1000)
  ptsddata = ptsddata+ptsddata2

for submission in ptsddata:
  collectData(submission, ptsd_dict)

print(str(len(ptsd_dict)) + " submissions have added to list")


https://api.pushshift.io/reddit/search/submission/?title="I was diagnosed with PTSD"&limit=1000&before=1612069200&subreddit=ptsd
https://api.pushshift.io/reddit/search/submission/?title="I was diagnosed with PTSD"&limit=1000&before=1378877692&subreddit=ptsd
39
https://api.pushshift.io/reddit/search/submission/?title="My PTSD"&limit=1000&before=1612069200&subreddit=ptsd
https://api.pushshift.io/reddit/search/submission/?title="My PTSD"&limit=1000&before=1593560398&subreddit=ptsd
200
https://api.pushshift.io/reddit/search/submission/?title="My PTSD"&limit=1000&before=1576215435&subreddit=ptsd
300
https://api.pushshift.io/reddit/search/submission/?title="My PTSD"&limit=1000&before=1562012318&subreddit=ptsd
400
https://api.pushshift.io/reddit/search/submission/?title="My PTSD"&limit=1000&before=1535813478&subreddit=ptsd
500
https://api.pushshift.io/reddit/search/submission/?title="My PTSD"&limit=1000&before=1480348328&subreddit=ptsd
600
https://api.pushshift.io/reddit/search/submission/?ti

### ADHD

I gather entries to be classified as ADHD. Users are classified as belonging to this class if they self-report themselves as diagnosed in a post in the subreddit "ADHD". I store the post that identifies them for the dataset. 1085 users were identified for this class.

In [ ]:
adhd_search = ['"I was diagnosed with ADHD"', '"My ADHD"', '"I am diagnosed with ADHD"']

adhd_dict = {}
adhddata = []

for item in adhd_search:
  adhddata2 = getAllPushshiftData(item, 1612069200, 'ADHD', 1000)
  adhddata = adhddata+adhddata2

for submission in adhddata:
  collectData(submission, adhd_dict)

print(str(len(adhd_dict)) + " submissions have added to list")


https://api.pushshift.io/reddit/search/submission/?title="I was diagnosed with ADHD"&limit=1000&before=1612069200&subreddit=ADHD
https://api.pushshift.io/reddit/search/submission/?title="I was diagnosed with ADHD"&limit=1000&before=1531282466&subreddit=ADHD
182
https://api.pushshift.io/reddit/search/submission/?title="I was diagnosed with ADHD"&limit=1000&before=1316155132&subreddit=ADHD
182
https://api.pushshift.io/reddit/search/submission/?title="My ADHD"&limit=1000&before=1612069200&subreddit=ADHD
https://api.pushshift.io/reddit/search/submission/?title="My ADHD"&limit=1000&before=1610652742&subreddit=ADHD
200
https://api.pushshift.io/reddit/search/submission/?title="My ADHD"&limit=1000&before=1609122005&subreddit=ADHD
300
https://api.pushshift.io/reddit/search/submission/?title="My ADHD"&limit=1000&before=1607775641&subreddit=ADHD
400
https://api.pushshift.io/reddit/search/submission/?title="My ADHD"&limit=1000&before=1606439500&subreddit=ADHD
500
https://api.pushshift.io/reddit/se

### Anxiety 

I gather entries to be classified as anxious. For anxious, I do not try to base on a specific diagnosis, but instead identify users that report struggling with anxiety in the subreddit "anxiety".  I store the post that identifies them for the dataset. 1963 users were identified for this class.

In [ ]:
anxiety_search = ['"I was diagnosed with anxiety"', '"My anxiety"', 
               '"I have anxiety"', '"I was diagnosed with GAD"']

anxiety_dict = {}
anxietydata = []

for item in anxiety_search:
  anxietydata2 = getAllPushshiftData(item, 1612069200, 'anxiety', 1000)
  anxietydata = anxietydata+anxietydata2

for submission in anxietydata:
  collectData(submission, anxiety_dict)

print(str(len(anxiety_dict)) + " submissions have added to list")

https://api.pushshift.io/reddit/search/submission/?title="I was diagnosed with anxiety"&limit=1000&before=1612069200&subreddit=anxiety
https://api.pushshift.io/reddit/search/submission/?title="I was diagnosed with anxiety"&limit=1000&before=1346298827&subreddit=anxiety
14
https://api.pushshift.io/reddit/search/submission/?title="My anxiety"&limit=1000&before=1612069200&subreddit=anxiety
https://api.pushshift.io/reddit/search/submission/?title="My anxiety"&limit=1000&before=1610842016&subreddit=anxiety
200
https://api.pushshift.io/reddit/search/submission/?title="My anxiety"&limit=1000&before=1609810736&subreddit=anxiety
300
https://api.pushshift.io/reddit/search/submission/?title="My anxiety"&limit=1000&before=1608626295&subreddit=anxiety
400
https://api.pushshift.io/reddit/search/submission/?title="My anxiety"&limit=1000&before=1607548814&subreddit=anxiety
500
https://api.pushshift.io/reddit/search/submission/?title="My anxiety"&limit=1000&before=1606509945&subreddit=anxiety
600
https

In [ ]:
anxiety_dict.keys()

dict_keys(['finessegangx', 'VanStrategist', 'polin_da', 'bobobaa', 'RyanJKaz', 'unofficialmoderator', '123ww55ssopa', 'exceptionallybland', 'kaupa_lupa', 'TripleGenesis', 'Daniaximehc', 'eddie90100', 'chunky_monkey96', '[deleted]', 'DaughterOfRageNLove_', 'keeperoftheworld69', 'iamreallytired123', 'throw4w4ygirl', 'Happy_Artichoke_108', 'OtherwiseCranberry88', 'bab_101', 'IamAlextric', 'SlipOutrageous5333', 'Aztec690', 'yungsaturn827', 'april_eleven', 'sylvia_bloodbath', 'bearface_stan', 'ehnotreallyokay', 'little-big-endian', 'MindsetMoment', 'EclecticCuriosity', 'Feeling-Yak7354', 'DeadHallow', 'Hacibay', 'f30bim', 'Secure-Imagination11', 'ChaseSpike11', 'winnie_bago', 'WisdomLove123', '_ActualHumanGarbage', 'Aromatic_Industry_73', 'Petrichor1995', 'lemonsandkevins', 'jahb0i', 'floorgang_gang', 'ksyrup', 'mtaylorcs', 'coffeegorl22', 'vanillacupcakess', 'ilovemycutechins', 'Sick_Bubbl3gum', 'Somepenguinsss', 'kaphwin', 'Eucharism', 'sweetpeabb', 'MrAlexander18', 'ilikesims4', 'ArcticE

## Protect Usernames for confidentiality purposes

In this section, I encode the usernames of those in the "experimental" classes in order to provide some confidentiality. 

In [ ]:
#delete users that appear in multiple dictoinaries.  I chose to do this because the overlap was less than 100
data_dictionaries = [anxiety_dict, adhd_dict, bpd_dict, bipolar_dict, dep_dict, ptsd_dict]
username_list = list(anxiety_dict.keys())+list(adhd_dict.keys()) + list(bpd_dict.keys()) + list( bipolar_dict.keys()) + list(dep_dict.keys()) + list(ptsd_dict.keys())

import collections
duplicates = [item for item, count in collections.Counter(username_list).items() if count > 1]

for entry in data_dictionaries:
  for duplicate in duplicates:
    if duplicate in entry.keys():
      entry.pop(duplicate)

#make new username_list 
username_list = list(anxiety_dict.keys())+list(adhd_dict.keys()) + list(bpd_dict.keys()) + list( bipolar_dict.keys()) + list(dep_dict.keys()) + list(ptsd_dict.keys())
print(len(username_list))
print(len(set(username_list)))

7994
7994


In [ ]:
def codeUsernames(names):
  """
  creates a dictionary mapping each name to a number representing it.  Returns the dictionary. 
  """
  username_set = set(names)
  #enumerate returns 2 variables, the count and the value of the item at that iteration 
  token_map = {name: i for i, name in enumerate(username_set)} 
  return token_map


In [ ]:
#dictionary of encoded usernames
username_encoded = codeUsernames(username_list)


In [ ]:
username_encoded.keys()

dict_keys(['yeedmylasthaww', 'Snoo_45237', 'fizztaa', 'SpectraRoot', '18860264018', 'poppyseedcat', 'wanderer_of_life', 'San_Sanich_02', 'stasieamore', 'TCMethod', '420aknigga', 'brookalaa', 'vilekreacher', 'Raging_Nerd', 'jemimahatstand', 'Silent_Avocado333', 'Smart_Coconut2227', 'LolGamer18', 'squidneym', 'BLTsandwich69', 'edomarc', 'niamhmn4', 'ocdflowey', 'aonoxoioeotoy', '_bipolar_polarbear_', 'AnkleSnatche', 'tonerslocers', 'poopematic', 'BlackFallout', 'PolarisWind', 'Extremebumpers', 'lusciousnoodle', 'muddleheadd', 'Important_Ad8329', 'MahThrowaway14', '_Raspootin_', 'Agreeable_Echo_5100', 'j_ayymeeb', 'agentgambino', 'kaitylettelee', 'BCassels', 'ElectionFast4284', 'aatayko', 'TheVeggieLife', 'dumidiotgirl', 'chillygooseuwu', 'polin_da', 'bumblebee147', 'bananapeel95', 'h4rdknocklife', 'lavenderhatchets', '-jolteon1-', 'ShinbrigGoku', 'IllInspection8', 'syobear', 'disorderedfiction', 'tohubohu8', 'schrute-on-shrooms', 'veronikuh', 'Gallifrey34', 'SoftBoiledPotatoChip', 'Longj

In [ ]:
def getName(val):
  """When given the number, return the username associated with it"""
  for key, value in username_encoded.items():
    if val == value:
      return key
  return "NaN"

In [ ]:
def anonymize_data(data):
  """
  takes in dictionary, and replaces the key (username) with the encoding of the username
  """
  old_names = list(data.keys())
  for name in old_names:
    new_key = username_encoded.get(name)
    data[new_key]=data.pop(name)

In [ ]:
# anonymizing all the data 

data_dictionaries = [anxiety_dict, adhd_dict, bpd_dict, bipolar_dict, dep_dict, ptsd_dict]

for entry in data_dictionaries:
  anonymize_data(entry)

dep_dict.keys()

dict_keys([778, 3984, 566, 2704, 3802, 5682, 6973, 660, 2109, 2749, 5276, 3356, 1292, 5032, 2430, 2981, 1384, 4082, 7215, 1698, 1876, 5501, 2938, 6870, 1575, 5085, 2292, 5349, 3978, 5940, 4487, 2852, 6240, 4601, 1152, 931, 6537, 636, 5136, 2807, 6303, 5998, 6376, 7177, 4067, 1230, 4532, 6531, 3979, 5415, 1842, 5126, 3301, 7018, 3653, 7515, 5332, 167, 7641, 728, 5377, 393, 7231, 4350, 592, 6078, 4587, 6370, 75, 6313, 5517, 3137, 5555, 4117, 6036, 907, 4710, 5273, 5622, 6573, 1316, 6145, 4351, 1996, 3555, 5410, 3498, 5626, 3601, 5985, 600, 3061, 3475, 537, 5528, 5390, 5185, 7799, 1534, 7003, 264, 3157, 7088, 661, 785, 7451, 3258, 3440, 5098, 7706, 6956, 6414, 4245, 2692, 6317, 4238, 5606, 6740, 6202, 1488, 6802, 706, 1740, 5308, 3918, 3494, 3577, 543, 4608, 4663, 5755, 1336, 6304, 4764, 6218, 7090, 2116, 982, 6285, 4057, 6212, 5402, 3829, 1653, 4174, 2742, 876, 5033, 7895, 7448, 6842, 4282, 2449, 6529, 7815, 7453, 4379, 47, 1722, 6189, 3166, 198, 1349, 1061, 6696, 4358, 6882, 7666, 6785,

## Creating dataframes for experimental cases 

I create a dataframe for each group and write it to file. 

In [ ]:
def createDataFrame(data):
  """
  Creates a dataframe from a dictionary, set up for submissions
  """
  return_df = pd.DataFrame.from_dict(data, orient='index', columns=
                                    ['sub_id', 'title', 'url', 'score', 'created', 'created_utc',
                                     'numComments', 'permalink', 'flair', 'selfext', 'subreddit'])
  return_df.reset_index(inplace=True)
  return_df = return_df.rename(columns = {'index': 'author'})
  return return_df

In [ ]:

anxiety_df = createDataFrame(anxiety_dict)
adhd_df = createDataFrame(adhd_dict)
bpd_df = createDataFrame(bpd_dict)
bipolar_df = createDataFrame(bipolar_dict)
dep_df = createDataFrame(dep_dict)
ptsd_df = createDataFrame(ptsd_dict)

ptsd_df.head()

author  sub_id  ...                                            selfext subreddit
0    7778  izgr81  ...  So I got an official detailed diagnosis from a...      ptsd
1     787  i5ijy1  ...  I went to a psychiatrist a day ago and after a...      ptsd
2    5895  hopdot  ...  I don’t really know how to handle the diagnosi...      ptsd
3    4880  hnub4q  ...  TW for brief abuse/addiction/death mention\n\n...      ptsd
4    3733  hmhqox  ...  in 2015, I was nearly murdered and from 2010-2...      ptsd

[5 rows x 12 columns]

In [ ]:
dep_df.head()

author  ...   subreddit
0    2477  ...  depression
1    7763  ...  depression
2    6624  ...  depression
3    2834  ...  depression
4    4168  ...  depression

[5 rows x 12 columns]

In [ ]:
cd drive/


/content/drive


In [ ]:
ls

MyDrive/  Shareddrives/


In [ ]:
cd MyDrive/

/content/drive/MyDrive


In [ ]:
 cd MentalHealthReddit/

/content/drive/MyDrive/MentalHealthReddit


In [ ]:
cd Data/

/content/drive/MyDrive/MentalHealthReddit/Data


In [ ]:
anxiety_df.to_csv('anxiety.csv')

In [ ]:
adhd_df.to_csv('adhd.csv')

In [ ]:
bpd_df.to_csv('bpd.csv')

In [ ]:
bipolar_df.to_csv('bipolar.csv')

In [ ]:
dep_df.to_csv('dep.csv')

In [ ]:
ptsd_df.to_csv('ptsd.csv')

# Get Data from other subreddits
I write helper functions to gather comments and submissions from the users identified in the above section. 


In [ ]:
def getOtherComments(author, after):
""" 
Get comment pushshift data (reddit data) for the given author after the given time. 
Returns the data
"""
  url = 'https://api.pushshift.io/reddit/search/comment/?author='+str(author)+'&after='+str(after)+'&size=100'
  print(url)
  r = requests.get(url)
  try:
    data = json.loads(r.text)
    return data['data']
  except ValueError:
    return ['NaN']
  return data['data']

In [ ]:
def getOtherSubmissions(author, after):
  """
  Get submission pushshift data (reddit data) for the given author after the given time. 
  Returns the data
  """

  url = 'https://api.pushshift.io/reddit/search/submission/?author='+str(author)+'&after='+str(after)+'&size=100'
  print(url)
  r = requests.get(url)
  print("passed request")
  try:
    data = json.loads(r.text)
    return data['data']
  except ValueError:
    return ['NaN']
  return data['data']

In [ ]:
 def getOtherCommentData(df):
   """
   Takes in a dataframe, and uses the author and date columns to search for more comments by that user
   Returns a dictionary with the new information
   """
  #takes in the dataframe 
  comment_dict = {}
  for user, time in zip(df['author'], df['created_utc']):
    username=getName(user)
    if (username != 'NaN') or (username != None): 
      data = getOtherComments(username, time)
      for comment in data:
        if comment != 'NaN':
          collectCommentData(comment, comment_dict)
  return comment_dict

In [ ]:
def getOtherSubmissionData(df):
   """
   Takes in a dataframe, and uses the author and date columns to search for more submissions by that user
   Returns a dictionary with the new information
   """
  submission_dict = {}
  for user, time in zip(df['author'], df['created_utc']):
    username=getName(user)
    data = getOtherSubmissions(username, time)
    for submission in data:
      if submission != 'NaN':
        #collectData(submission, submission_dict)
        collectOtherSubmissionData(submission, submission_dict)
  return submission_dict

In [ ]:
def anonymize_submissions(data):
  """
  Takes in a dictionary, anonymizes the username
  """
  for key in data:
    tempname = data.get(key)[0]
    codename = username_encoded.get(tempname)
    data.get(key)[0] = codename


In [ ]:
alter_anxietycom = getOtherCommentData(anxiety_df)

https://api.pushshift.io/reddit/search/comment/?author=finessegangx&after=1605823041&size=100
https://api.pushshift.io/reddit/search/comment/?author=VanStrategist&after=1601773048&size=100
https://api.pushshift.io/reddit/search/comment/?author=polin_da&after=1585360223&size=100
https://api.pushshift.io/reddit/search/comment/?author=bobobaa&after=1581643539&size=100
https://api.pushshift.io/reddit/search/comment/?author=RyanJKaz&after=1576678024&size=100
https://api.pushshift.io/reddit/search/comment/?author=unofficialmoderator&after=1547585723&size=100
https://api.pushshift.io/reddit/search/comment/?author=exceptionallybland&after=1572559957&size=100
https://api.pushshift.io/reddit/search/comment/?author=kaupa_lupa&after=1552233921&size=100
https://api.pushshift.io/reddit/search/comment/?author=TripleGenesis&after=1549901547&size=100
https://api.pushshift.io/reddit/search/comment/?author=Daniaximehc&after=1548195120&size=100
https://api.pushshift.io/reddit/search/comment/?author=eddie9

In [ ]:
alter_anxietysub = getOtherSubmissionData(anxiety_df)


https://api.pushshift.io/reddit/search/submission/?author=finessegangx&after=1605823041&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=VanStrategist&after=1601773048&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=polin_da&after=1585360223&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=bobobaa&after=1581643539&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=RyanJKaz&after=1576678024&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=unofficialmoderator&after=1547585723&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=exceptionallybland&after=1572559957&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=kaupa_lupa&after=1552233921&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=TripleGenesis&after=1549901547&size=100
passed 

In [ ]:
anonymize_submissions(alter_anxietysub)

In [ ]:
anonymize_submissions(alter_anxietycom)

In [ ]:
def createDataFrameSubs(data):
  """
  Takes in a dictionary and returns a dataframe, set up for Submissions
  """

  return_df = pd.DataFrame.from_dict(data, orient='index', columns=
                                    ['author', 'title', 'url', 'score', 'created', 'created_utc',
                                     'numComms', 'permalink', 'flair', 'selftex', 'subreddit'])
  return_df.reset_index(inplace=True)
  return_df = return_df.rename(columns = {'index': 'sub_id'})
  return return_df


In [ ]:
def createDataFrameComments(data):
  """
  Takes in a dictionary and returns a dataframe, set up for Comments
  """
  return_df = pd.DataFrame.from_dict(data, orient='index', columns=
                                    ['author', 'score', 'created', 'created_utc',
                                     'url', 'body', 'subreddit'])
  return_df.reset_index(inplace=True)
  return_df = return_df.rename(columns = {'index': 'com_id'})
  return return_df


In [ ]:
anxiety_subs_df = createDataFrameSubs(alter_anxietysub)
anxiety_subs_df.head()

sub_id  ...           subreddit
0  lhukth  ...          Leximulaaa
1  lm55xj  ...             opiates
2  mf6nri  ...           JessVinci
3  mkvmp8  ...  HappyEndingMassage
4  mmf49y  ...  HappyEndingMassage

[5 rows x 12 columns]

In [ ]:
anxiety_coms_df = createDataFrameComments(alter_anxietycom)
anxiety_coms_df.head(20)

com_id  ...            subreddit
0   gcvp6f9  ...              Anxiety
1   gcw1cwq  ...              latinas
2   gcw94v3  ...              Anxiety
3   gcyec2m  ...  DaniellePertusiello
4   gcyoq7d  ...              Anxiety
5   ghiu03o  ...  damngoodinterracial
6   ghiv9vc  ...   InterracialTeenSex
7   gmzegtw  ...           Leximulaaa
8   gmzwizx  ...           Leximulaaa
9   gmzwke5  ...           Leximulaaa
10  gmzxsvb  ...      laurenpisciotta
11  gn2xkbf  ...           Leximulaaa
12  gnt81uc  ...              opiates
13  gntdd4p  ...              opiates
14  gnte4rg  ...              opiates
15  gnteksr  ...         OpiateChurch
16  gnts22i  ...    teenswithtanlines
17  gnty2c4  ...              Anxiety
18  gswurkj  ...     McKinzieValdezzz
19  gsy9w3l  ...           TikTokNude

[20 rows x 8 columns]

In [ ]:
from google.colab import drive

In [ ]:
anxiety_subs_df.to_csv('anxiey_subs.csv')

In [ ]:

anxiety_coms_df.to_csv('anxiety_coms.csv')

In [ ]:
alter_ptsdcom = getOtherCommentData(ptsd_df)

https://api.pushshift.io/reddit/search/comment/?author=off0noff&after=1601027824&size=100
https://api.pushshift.io/reddit/search/comment/?author=-NeoRoseBud-&after=1596822933&size=100
https://api.pushshift.io/reddit/search/comment/?author=alicesann&after=1594389432&size=100
https://api.pushshift.io/reddit/search/comment/?author=not_monica&after=1594259395&size=100
https://api.pushshift.io/reddit/search/comment/?author=beatmethefuckupbro&after=1594073469&size=100
https://api.pushshift.io/reddit/search/comment/?author=TheActualMonthOfJune&after=1592288923&size=100
https://api.pushshift.io/reddit/search/comment/?author=yodawastall&after=1590522228&size=100
https://api.pushshift.io/reddit/search/comment/?author=thetreewasblue&after=1587969634&size=100
https://api.pushshift.io/reddit/search/comment/?author=w0rldsosnow&after=1576464624&size=100
https://api.pushshift.io/reddit/search/comment/?author=Fatsohuggingbear&after=1576842312&size=100
https://api.pushshift.io/reddit/search/comment/?aut

In [ ]:
alter_ptsdsub = getOtherSubmissionData(ptsd_df)

https://api.pushshift.io/reddit/search/submission/?author=off0noff&after=1601027824&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=-NeoRoseBud-&after=1596822933&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=alicesann&after=1594389432&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=not_monica&after=1594259395&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=beatmethefuckupbro&after=1594073469&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=TheActualMonthOfJune&after=1592288923&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=yodawastall&after=1590522228&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=thetreewasblue&after=1587969634&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=w0rldsosnow&after=1576464624&size=100
pa

In [ ]:
anonymize_submissions(alter_ptsdcom)
anonymize_submissions(alter_ptsdsub)

In [ ]:
ptsd_subs_df = createDataFrameSubs(alter_ptsdsub)
ptsd_coms_df = createDataFrameComments(alter_ptsdcom)
ptsd_subs_df.head(10)

sub_id  ...             subreddit
0  j0jgjy  ...  talesfromcallcenters
1  j49w03  ...  talesfromcallcenters
2  j5fxu5  ...  talesfromcallcenters
3  jftmzb  ...           callcentres
4  kohnh9  ...            offmychest
5  koig5s  ...        TrueOffMyChest
6  kpa5ps  ...         mobilelegends
7  ktfgsi  ...      CallOfDutyMobile
8  kwsoav  ...      CallOfDutyMobile
9  l6t52c  ...                Advice

[10 rows x 12 columns]

In [ ]:
ptsd_subs_df.to_csv('ptsd_subs.csv')

In [ ]:
ptsd_coms_df.to_csv('ptsd_coms.csv')

In [ ]:
alter_bipolarcom = getOtherCommentData(bipolar_df)

https://api.pushshift.io/reddit/search/comment/?author=DaemonWorshiper&after=1612069164&size=100
https://api.pushshift.io/reddit/search/comment/?author=aloneagainnaturally1&after=1606921104&size=100
https://api.pushshift.io/reddit/search/comment/?author=cerebral_thunders&after=1612062258&size=100
https://api.pushshift.io/reddit/search/comment/?author=mo282&after=1612053523&size=100
https://api.pushshift.io/reddit/search/comment/?author=jibberjabbery&after=1604358114&size=100
https://api.pushshift.io/reddit/search/comment/?author=CurveGalaxy&after=1610675980&size=100
https://api.pushshift.io/reddit/search/comment/?author=picodegalloyum7&after=1604286638&size=100
https://api.pushshift.io/reddit/search/comment/?author=midheaven111&after=1609342272&size=100
https://api.pushshift.io/reddit/search/comment/?author=twotimesbi&after=1612042553&size=100
https://api.pushshift.io/reddit/search/comment/?author=throwawayaccnt34567&after=1612042393&size=100
https://api.pushshift.io/reddit/search/comm

In [ ]:
alter_bipolarsub = getOtherSubmissionData(bipolar_df)

https://api.pushshift.io/reddit/search/submission/?author=DaemonWorshiper&after=1612069164&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=aloneagainnaturally1&after=1606921104&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=cerebral_thunders&after=1612062258&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=mo282&after=1612053523&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=jibberjabbery&after=1604358114&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=CurveGalaxy&after=1610675980&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=picodegalloyum7&after=1604286638&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=midheaven111&after=1609342272&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=twotimesbi&after=1612042553&size=1

In [ ]:
anonymize_submissions(alter_bipolarcom)
anonymize_submissions(alter_bipolarsub)

In [ ]:
bipolar_subs_df = createDataFrameSubs(alter_bipolarsub)
bipolar_coms_df = createDataFrameComments(alter_bipolarcom)

bipolar_subs_df.head(10)

sub_id  ...            subreddit
0  l9sdjl  ...  ForwardsFromKlandma
1  lq2kbr  ...    carnivorousplants
2  lwg49b  ...    carnivorousplants
3  mvoy4o  ...             SafeMoon
4  mw5luq  ...             SafeMoon
5  mz106g  ...             SafeMoon
6  mz1vdq  ...             SafeMoon
7  n4ugde  ...             SafeMoon
8  nrdbc9  ...             trustapp
9  k7994d  ...        BipolarReddit

[10 rows x 12 columns]

In [ ]:
bipolar_coms_df.to_csv('bipolar_coms.csv')

In [ ]:
bipolar_subs_df.to_csv('bipolar_subs.csv')

In [ ]:
alter_bpdcom = getOtherCommentData(bpd_df)

https://api.pushshift.io/reddit/search/comment/?author=-artistoverhere-&after=1612069153&size=100
https://api.pushshift.io/reddit/search/comment/?author=AQuietBorderline&after=1612068753&size=100
https://api.pushshift.io/reddit/search/comment/?author=retrogradecapricorn&after=1611308290&size=100
https://api.pushshift.io/reddit/search/comment/?author=treestandingbrow&after=1612065962&size=100
https://api.pushshift.io/reddit/search/comment/?author=tatoo1ne&after=1612065290&size=100
https://api.pushshift.io/reddit/search/comment/?author=StephanieSpoiler&after=1612065273&size=100
https://api.pushshift.io/reddit/search/comment/?author=Ca3Al2Si3O12&after=1612064981&size=100
https://api.pushshift.io/reddit/search/comment/?author=throwaway3098439&after=1612062749&size=100
https://api.pushshift.io/reddit/search/comment/?author=youneedmeat&after=1611853054&size=100
https://api.pushshift.io/reddit/search/comment/?author=Buckmiester2017&after=1612062154&size=100
https://api.pushshift.io/reddit/sea

In [ ]:
alter_bpdsub = getOtherSubmissionData(bpd_df)

https://api.pushshift.io/reddit/search/submission/?author=-artistoverhere-&after=1612069153&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=AQuietBorderline&after=1612068753&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=retrogradecapricorn&after=1611308290&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=treestandingbrow&after=1612065962&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=tatoo1ne&after=1612065290&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=StephanieSpoiler&after=1612065273&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=Ca3Al2Si3O12&after=1612064981&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=throwaway3098439&after=1612062749&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=youneedmeat&after=16118

In [ ]:
anonymize_submissions(alter_bpdcom)
anonymize_submissions(alter_bpdsub)

In [ ]:
bpd_subs_df = createDataFrameSubs(alter_bpdsub)
bpd_coms_df = createDataFrameComments(alter_bpdcom)
bpd_subs_df.head(10)

sub_id  ...           subreddit
0  lc0zcg  ...                 BPD
1  lfi3mf  ...                 BPD
2  ljuzpq  ...                 BPD
3  lmni1n  ...  psychologyresearch
4  lmurha  ...                 BPD
5  lnjowt  ...        SuicideWatch
6  lpy1jg  ...          depression
7  m0uk1b  ...                 BPD
8  m0upvh  ...                 BPD
9  m1biah  ...                 BPD

[10 rows x 12 columns]

In [ ]:
bpd_subs_df.to_csv('bpd_subs.csv')

In [ ]:
bpd_coms_df.to_csv('bpd_coms.csv')

In [ ]:
alter_adhdcom = getOtherCommentData(adhd_df)

https://api.pushshift.io/reddit/search/comment/?author=aboze04&after=1612026856&size=100
https://api.pushshift.io/reddit/search/comment/?author=Vibrantical&after=1611949543&size=100
https://api.pushshift.io/reddit/search/comment/?author=Mk_it_so&after=1611253679&size=100
https://api.pushshift.io/reddit/search/comment/?author=paul-pryor&after=1611247677&size=100
https://api.pushshift.io/reddit/search/comment/?author=straymender&after=1609613007&size=100
https://api.pushshift.io/reddit/search/comment/?author=kanjobanjo17&after=1608226638&size=100
https://api.pushshift.io/reddit/search/comment/?author=SylviaTheKitty&after=1606931085&size=100
https://api.pushshift.io/reddit/search/comment/?author=kaprielmoon&after=1606402994&size=100
https://api.pushshift.io/reddit/search/comment/?author=Jayu2&after=1606220263&size=100
https://api.pushshift.io/reddit/search/comment/?author=universemessages&after=1603959680&size=100
https://api.pushshift.io/reddit/search/comment/?author=sexi_squidward&after

In [ ]:
alter_adhdsub = getOtherSubmissionData(adhd_df)

https://api.pushshift.io/reddit/search/submission/?author=aboze04&after=1612026856&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=Vibrantical&after=1611949543&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=Mk_it_so&after=1611253679&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=paul-pryor&after=1611247677&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=straymender&after=1609613007&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=kanjobanjo17&after=1608226638&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=SylviaTheKitty&after=1606931085&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=kaprielmoon&after=1606402994&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=Jayu2&after=1606220263&size=100
passed request
https://api

In [ ]:
anonymize_submissions(alter_adhdcom)
anonymize_submissions(alter_adhdsub)

In [ ]:
adhd_subs_df = createDataFrameSubs(alter_adhdsub)
adhd_coms_df = createDataFrameComments(alter_adhdcom)
adhd_subs_df.head(10)

sub_id  ...    subreddit
0  l8pbdd  ...         IDAP
1  l8r6bs  ...         ADHD
2  l750h4  ...  snowshoeing
3  ln7mee  ...   freediving
4  m2jg04  ...         dogs
5  m2jmtl  ...         dogs
6  ndgrl5  ...       Lichen
7  kpu68m  ...         ADHD
8  kqj8ah  ...     BreakUps
9  kr7she  ...      Petloss

[10 rows x 12 columns]

In [ ]:
adhd_subs_df.to_csv('adhd_subs.csv')

In [ ]:
adhd_coms_df.to_csv('adhd_coms.csv')

In [ ]:
dep_df.head()

author  ...   subreddit
0    2277  ...  depression
1     529  ...  depression
2    5046  ...  depression
3    6557  ...  depression
4    4683  ...  depression

[5 rows x 12 columns]

In [ ]:
alter_depcom = getOtherCommentData(dep_df)

https://api.pushshift.io/reddit/search/comment/?author=Funny_Eyebrow&after=1606752033&size=100
https://api.pushshift.io/reddit/search/comment/?author=leafy_and_lethal&after=1602421299&size=100
https://api.pushshift.io/reddit/search/comment/?author=celtree03&after=1598779788&size=100
https://api.pushshift.io/reddit/search/comment/?author=koobtooboob&after=1598770463&size=100
https://api.pushshift.io/reddit/search/comment/?author=sometimesitbelikedat&after=1595805695&size=100
https://api.pushshift.io/reddit/search/comment/?author=ugly_worthless_trash&after=1595792408&size=100
https://api.pushshift.io/reddit/search/comment/?author=DeadlyDan123&after=1594688115&size=100
https://api.pushshift.io/reddit/search/comment/?author=Ruby_Lowe&after=1589411320&size=100
https://api.pushshift.io/reddit/search/comment/?author=Chrisrawraw&after=1586678766&size=100
https://api.pushshift.io/reddit/search/comment/?author=la_d0xa&after=1585072717&size=100
https://api.pushshift.io/reddit/search/comment/?auth

In [ ]:
alter_depsub = getOtherSubmissionData(dep_df)

https://api.pushshift.io/reddit/search/submission/?author=Funny_Eyebrow&after=1606752033&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=leafy_and_lethal&after=1602421299&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=celtree03&after=1598779788&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=koobtooboob&after=1598770463&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=sometimesitbelikedat&after=1595805695&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=ugly_worthless_trash&after=1595792408&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=DeadlyDan123&after=1594688115&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=Ruby_Lowe&after=1589411320&size=100
passed request
https://api.pushshift.io/reddit/search/submission/?author=Chrisrawraw&after=1586678766&siz

In [ ]:
anonymize_submissions(alter_depcom)


In [ ]:
anonymize_submissions(alter_depsub)

In [ ]:
dep_subs_df = createDataFrameSubs(alter_depsub)

In [ ]:
dep_subs_df.head()

sub_id  ...            subreddit
0  k40gmp  ...  relationship_advice
1  k416rs  ...  relationship_advice
2  k41j0f  ...  relationship_advice
3  k4b7mu  ...  relationship_advice
4  k4rqs5  ...  relationship_advice

[5 rows x 12 columns]

In [ ]:

dep_coms_df = createDataFrameComments(alter_depcom)

In [ ]:
dep_coms_df.head()

com_id  ...            subreddit
0  ge69z36  ...  relationship_advice
1  geaf0o2  ...  relationship_advice
2  geafutc  ...  relationship_advice
3  geagp0q  ...  relationship_advice
4  geaj1xa  ...  relationship_advice

[5 rows x 8 columns]

In [ ]:
dep_subs_df.head()

sub_id  ...            subreddit
0  k40gmp  ...  relationship_advice
1  k416rs  ...  relationship_advice
2  k41j0f  ...  relationship_advice
3  k4b7mu  ...  relationship_advice
4  k4rqs5  ...  relationship_advice

[5 rows x 12 columns]

In [ ]:
ls

dep_subs.csv  drive/  sample_data/


In [ ]:
cd MyDrive/MentalHealthReddit/Data/

/content/drive/MyDrive/MentalHealthReddit/Data


In [ ]:
dep_subs_df.to_csv('dep_subs.csv')

In [ ]:
dep_coms_df.to_csv('dep_coms.csv')

## Get Control Group

I identified subreddits that the users above posted to (analysis part in mentalhealthredditanalysis.ipynb), and gather users from those subreddits to be the "control" group. I create new helper functions focused on gather data from those subreddits, and then gathering more data from identified users. 

In [ ]:
control_subreddits = ['AskReddit',
 'AmItheAsshole',
 'teenagers',
 'relationship_advice',
 'relationships',
 'aww',
 'offmychest',
 'NoStupidQuestions',
 'unpopularopinion',
 'pics',
 'PurplePillDebate',
 'todayilearned',
 'Advice',
 'AskTeenGirls',
 'bois',
 'AskWomen',
 'hiphopheads',
 'trees',
 'PokemonTCG',
 'stopdrinking',
 'funny',
 'gonewild',
 'worldnews',
 'MaddenUltimateTeam',
 'loseit',
 'WTF',
 'childfree',
 'Depop',
 'trumpet',
 'lawofattraction',
 'AskWomenOver30',
 'Hamilton',
 'askanincel',
 'homestuck',
 'asktrp',
 'Aquariums',
 'PoliticalCompassMemes',
 'sex',
 'MakeNewFriendsHere',
 'Eberron',
 'AskDocs',
 'asktransgender',
 'Showerthoughts',
 'randomactsofamazon',
 'MakeupAddiction',
 'actuallesbians',
 'RealEstate',
 'CBD',
 'politics',
 'ImaginaryHorrors',
 'survivor',
 'FreeCompliments',
 'thesims',
 'WWEGames',
 'memes',
 'ExNoContact',
 'UnsentLetters',
 'dogecoin',
 'weed',
 'AskMen',
 'confession',
 'nba',
 'GERD',
 'intj',
 'gifs',
 'JUSTNOMIL',
 'leagueoflegends',
 'Hashimotos',
 'TumblrInAction',
 'forhonor',
 'TeenMomOGandTeenMom2',
 'mildlyinteresting',
 'TwoXChromosomes',
 'personalfinance',
 'legaladvice',
 'TooAfraidToAsk',
 'Parenting',
 'playboicarti',
 'Coronavirus',
 'horror',
 'gaming',
 'Needafriend',
 'medical',
 'CasualConversation',
 'de',
 'india',
 'dogs',
 'Drugs',
 'confessions',
 'cats',
 'RoastMe',
 'Narcolepsy',
 'nyc',
 'videos',
 'tattoos',
 'bisexual',
 'news',
 'wholesomememes',
 'trashy',
 'AMA',
 'short',
 'Wishlist',
 'lgbt',
 'sewing',
 'ChoosingBeggars',
 'dating',
 'entwives',
 'prettyaltgirls',
 'LawofAttractionAdvice',
 'acne',
 'traaaaaaannnnnnnnnns',
 'AnimalCrossing',
 'mildlyinfuriating',
 'MadeOfStyrofoam',
 'PewdiepieSubmissions',
 'narcissisticparents',
 'Epilepsy',
 'budgies',
 'TrueOffMyChest',
 'RedDeadOnline',
 'RedditSessions',
 'tifu',
 'AskOuija',
 'PublicFreakout',
 'interestingasfuck',
 'Cringetopia',
 'BreakUps',
 'college',
 'bettafish',
 'starterpacks',
 'SubredditDrama',
 'ftm',
 'curlyhair',
 'AdviceAnimals',
 'rant',
 'piercing',
 'deadbydaylight',
 'SafeMoon',
 'socialskills',
 'Tinder',
 'oddlysatisfying',
 'insanepeoplefacebook',
 'INTP',
 'DunderMifflin',
 'MechanicalKeyboards',
 'distantsocializing',
 'Vent',
 'polyamory',
 'jobs',
 'careerguidance',
 'pregnant',
 'MorbidReality',
 'conspiracy',
 'Psychic',
 'formula1',
 'tipofmytongue',
 'SkincareAddiction',
 'Osana',
 'NoFap',
 'nextfuckinglevel',
 'explainlikeimfive',
 'niceguys',
 'changemyview',
 'CasualUK',
 'askwomenadvice',
 'movies',
 'askgaybros',
 'MtF',
 '2meirl4meirl',
 'MadeMeSmile',
 'OldSchoolCool',
 'medical_advice',
 'LifeProTips',
 'service_dogs',
 'CrohnsDisease',
 'AskAnAmerican',
 'ChronicPain',
 'NintendoSwitch',
 'apexlegends',
 'DoesAnybodyElse',
 'cursedcomments',
 'books',
 'gardening',
 'dating_advice',
 'amiugly',
 'iamatotalpieceofshit',
 'food',
 'Wellthatsucks',
 'writing',
 'Conservative',
 'witchcraft',
 'fasting',
 'progresspics',
 'me_irl',
 '4595',
 'dankmemes',
 'birthcontrol',
 'commandandconquer',
 'Minecraft',
 'wallstreetbets',
 'TheMandalorianTV',
 'morbidquestions',
 'asexuality',
 'harrypotter',
 'IdiotsInCars',
 'FortNiteBR',
 'blackdesertonline',
 'pornfree',
 'Christianity',
 'TheYouShow',
 'Meditation',
 'leaves',
 'BeautyGuruChatter',
 'Random_Acts_Of_Amazon',
 'Overwatch',
 'FortniteCompetitive',
 'Psychonaut',
 'ask',
 'GlobalOffensive',
 'pcmasterrace',
 'WhitePeopleTwitter',
 'Rabbits',
 'houseplants',
 'Supplements',
 'whatisthisthing',
 'egg_irl',
 'StarWars',
 'Sims4',
 'selfimprovement',
 'techsupport',
 'selfie',
 'Teachers',
 '2007scape',
 'lonely',
 'pan_media',
 'shrooms',
 'creepyPMs',
 'vegan',
 'Fitness',
 'DecidingToBeBetter',
 'apple',
 'self',
 'spirituality',
 'TikTokCringe',
 'nfl',
 'facepalm',
 'Marriage',
 'languagelearning',
 'titanfolk',
 'Chiraqology',
 'keto',
 'Music',
 'AnimalsOnReddit',
 'suggestmeabook',
 'PsilocybinMushrooms',
 'microdosing',
 'Periods',
 'infp',
 'antiwork',
 'Empaths',
 'kroger',
 'PCOS',
 'AskUK',
 'wow',
 'mbti',
 'AskAstrologers',
 'anime',
 'Sneakers',
 'LSD',
 'stocks',
 'CallOfDutyMobile',
 'h3h3productions',
 'migraine',
 'masskillers',
 'exmuslim',
 'DnD',
 'peaceCorpsCoding',
 'blackcats',
 'GMT400',
 'r4r',
 'EDAnonymous',
 'buildapc',
 '196',
 'AreTheStraightsOK',
 'Dentistry',
 'ibs',
 'Screenwriting',
 'COVID19positive',
 'Crystals',
 'FemaleDatingStrategy',
 'delta8',
 'fantasyfootball',
 'hockey',
 'chat',
 'recruitinghell',
 'UFOs',
 'Hellenism',
 'Codependency',
 'RocketLeagueExchange',
 'breakingmom',
 'CryptoCurrency',
 'stupidpol',
 'PokemonGoRaids',
 'polls',
 'introvert',
 'ClashOfClans',
 'TaylorSwift',
 'indonesia',
 'CysticFibrosis',
 'sportsbook',
 'summonerswar',
 'Amoledbackgrounds',
 'SamONellaAcademy',
 'thebachelor',
 'TallTeenagers',
 'yungblud',
 'soccer',
 'SquaredCircle',
 'Mcat',
 'benzorecovery',
 'NoFeeAC',
 'Sat',
 'cyberpunkgame',
 'CoronavirusUK',
 'FashionReps',
 'Repsneakers',
 'DMT',
 'HeadphoneAdvice',
 'AmongUs',
 'makinghiphop',
 'FemaleLevelUpStrategy',
 'redscarepod',
 'SimDemocracy',
 'DrMartens',
 'Petloss',
 'KGATLW',
 'GoForGold',
 'TransTryouts',
 'Snus',
 'amcstock',
 'onewordeach',
 'MoneyDiariesACTIVE']

In [ ]:
len(control_subreddits)

342

In [ ]:
def getUserPushData(subreddit, before):
  """
  Returns comment data from Pushshift from the specfied subreddit before the specified time; aggregates author
  """
   url = 'https://api.pushshift.io/reddit/search/comment/?before='+str(before)+'&subreddit='+str(subreddit)+'&aggs=author&agg_size=100'
   print(url)
   r = requests.get(url)
   data = json.loads(r.text)
   return data['data']


In [ ]:
def getUserPushData2(subreddit, before):
  """
  Returns comment data from Pushshift from the specfied subreddit before the specified time
  """
   url = 'https://api.pushshift.io/reddit/search/comment/?before='+str(before)+'&subreddit='+str(subreddit)+'&size=100'
   print(url)
   r = requests.get(url)
   data = json.loads(r.text)
   return data['data']

In [ ]:
def getAllUserPushData(subreddit, before, size):
"""
Runs repeated searches of Pushshift until the desired length of data is reached
"""

  returndata = getUserPushData2(subreddit, before)
  length = len(returndata)
  newdata = [1]
  while (length < size) and (len(newdata) !=0): 
    newdata = getUserPushData2(subreddit, returndata[-1]['created_utc'])
    returndata = returndata + newdata
    length = len(returndata)
    print(len(returndata))
    time.sleep(1)
  return returndata

In [ ]:
def collectNewUserData(submission, stats):
  """
  Takes in a submission, and the dictionary you wanat to append the information too
  """
  try:    
    author = submission['author']
  except KeyError:
    return
  #created = datetime.datetime.fromtimestamp(submission['created_utc']) #1520561700.0
  try:
    created_utc = submission['created_utc']
  except KeyError:
    return
  #subData = [created_utc, created]
  stats[author] = created_utc


### Get control data

I go through the identified subreddits, and collect usernames for users who post there. 

In [ ]:
user_dict = {}
for subreddit in control_subreddits[:50]:
  userdata = getAllUserPushData(subreddit, 1612069200, 1500)
  for submission in userdata:
    collectNewUserData(submission, user_dict)

https://api.pushshift.io/reddit/search/comment/?before=1612069200&subreddit=AskReddit&size=100
https://api.pushshift.io/reddit/search/comment/?before=1612069161&subreddit=AskReddit&size=100
200
https://api.pushshift.io/reddit/search/comment/?before=1612069113&subreddit=AskReddit&size=100
300
https://api.pushshift.io/reddit/search/comment/?before=1612069078&subreddit=AskReddit&size=100
400
https://api.pushshift.io/reddit/search/comment/?before=1612069033&subreddit=AskReddit&size=100
500
https://api.pushshift.io/reddit/search/comment/?before=1612068990&subreddit=AskReddit&size=100
600
https://api.pushshift.io/reddit/search/comment/?before=1612068947&subreddit=AskReddit&size=100
700
https://api.pushshift.io/reddit/search/comment/?before=1612068896&subreddit=AskReddit&size=100
800
https://api.pushshift.io/reddit/search/comment/?before=1612068846&subreddit=AskReddit&size=100
900
https://api.pushshift.io/reddit/search/comment/?before=1612068799&subreddit=AskReddit&size=100
1000
https://api.p

In [ ]:

len(user_dict)

33069

In [ ]:
control_subreddits.remove('SafeMoon') #was only recently created 

In [ ]:
for subreddit in control_subreddits[50:100]:
  userdata = getAllUserPushData(subreddit, 1612069200, 1500)
  for submission in userdata:
    collectNewUserData(submission, user_dict)

https://api.pushshift.io/reddit/search/comment/?before=1612069200&subreddit=survivor&size=100
https://api.pushshift.io/reddit/search/comment/?before=1612063573&subreddit=survivor&size=100
200
https://api.pushshift.io/reddit/search/comment/?before=1612059638&subreddit=survivor&size=100
300
https://api.pushshift.io/reddit/search/comment/?before=1612055826&subreddit=survivor&size=100
400
https://api.pushshift.io/reddit/search/comment/?before=1612051655&subreddit=survivor&size=100
500
https://api.pushshift.io/reddit/search/comment/?before=1612048278&subreddit=survivor&size=100
600
https://api.pushshift.io/reddit/search/comment/?before=1612043778&subreddit=survivor&size=100
700
https://api.pushshift.io/reddit/search/comment/?before=1612041017&subreddit=survivor&size=100
800
https://api.pushshift.io/reddit/search/comment/?before=1612036299&subreddit=survivor&size=100
900
https://api.pushshift.io/reddit/search/comment/?before=1612033233&subreddit=survivor&size=100
1000
https://api.pushshift.i

In [ ]:
len(user_dict)

66926

In [ ]:
for subreddit in control_subreddits[100:150]:
  userdata = getAllUserPushData(subreddit, 1612069200, 1500)
  for submission in userdata:
    collectNewUserData(submission, user_dict)

https://api.pushshift.io/reddit/search/comment/?before=1612069200&subreddit=short&size=100
https://api.pushshift.io/reddit/search/comment/?before=1612037497&subreddit=short&size=100
200
https://api.pushshift.io/reddit/search/comment/?before=1611982534&subreddit=short&size=100
300
https://api.pushshift.io/reddit/search/comment/?before=1611936278&subreddit=short&size=100
400
https://api.pushshift.io/reddit/search/comment/?before=1611899847&subreddit=short&size=100
500
https://api.pushshift.io/reddit/search/comment/?before=1611867569&subreddit=short&size=100
600
https://api.pushshift.io/reddit/search/comment/?before=1611846852&subreddit=short&size=100
700
https://api.pushshift.io/reddit/search/comment/?before=1611792944&subreddit=short&size=100
800
https://api.pushshift.io/reddit/search/comment/?before=1611470227&subreddit=short&size=100
900
https://api.pushshift.io/reddit/search/comment/?before=1611446067&subreddit=short&size=100
1000
https://api.pushshift.io/reddit/search/comment/?befor

IndexError: ignored

In [ ]:
len(user_dict)

90057

In [ ]:
for subreddit in control_subreddits[137:200]:
  userdata = getAllUserPushData(subreddit, 1612069200, 800)
  for submission in userdata:
    collectNewUserData(submission, user_dict)

https://api.pushshift.io/reddit/search/comment/?before=1612069200&subreddit=socialskills&size=100
https://api.pushshift.io/reddit/search/comment/?before=1612059152&subreddit=socialskills&size=100
200
https://api.pushshift.io/reddit/search/comment/?before=1612049795&subreddit=socialskills&size=100
300
https://api.pushshift.io/reddit/search/comment/?before=1612040529&subreddit=socialskills&size=100
400
https://api.pushshift.io/reddit/search/comment/?before=1612031883&subreddit=socialskills&size=100
500
https://api.pushshift.io/reddit/search/comment/?before=1612024496&subreddit=socialskills&size=100
600
https://api.pushshift.io/reddit/search/comment/?before=1612015577&subreddit=socialskills&size=100
700
https://api.pushshift.io/reddit/search/comment/?before=1612003259&subreddit=socialskills&size=100
800
https://api.pushshift.io/reddit/search/comment/?before=1612069200&subreddit=Tinder&size=100
https://api.pushshift.io/reddit/search/comment/?before=1612067249&subreddit=Tinder&size=100
200


In [ ]:
len(user_dict)

112595

In [ ]:
for subreddit in control_subreddits[200:300]:
  userdata = getAllUserPushData(subreddit, 1612069200, 600)
  for submission in userdata:
    collectNewUserData(submission, user_dict)

https://api.pushshift.io/reddit/search/comment/?before=1612069200&subreddit=morbidquestions&size=100
https://api.pushshift.io/reddit/search/comment/?before=1612049354&subreddit=morbidquestions&size=100
200
https://api.pushshift.io/reddit/search/comment/?before=1612034310&subreddit=morbidquestions&size=100
300
https://api.pushshift.io/reddit/search/comment/?before=1612013197&subreddit=morbidquestions&size=100
400
https://api.pushshift.io/reddit/search/comment/?before=1611981731&subreddit=morbidquestions&size=100
500
https://api.pushshift.io/reddit/search/comment/?before=1611956162&subreddit=morbidquestions&size=100
600
https://api.pushshift.io/reddit/search/comment/?before=1612069200&subreddit=asexuality&size=100
https://api.pushshift.io/reddit/search/comment/?before=1612060531&subreddit=asexuality&size=100
200
https://api.pushshift.io/reddit/search/comment/?before=1612051131&subreddit=asexuality&size=100
300
https://api.pushshift.io/reddit/search/comment/?before=1612043550&subreddit=as

In [ ]:
for subreddit in control_subreddits[300:]:
  userdata = getAllUserPushData(subreddit, 1612069200, 200)
  for submission in userdata:
    collectNewUserData(submission, user_dict)

https://api.pushshift.io/reddit/search/comment/?before=1612069200&subreddit=stupidpol&size=100
https://api.pushshift.io/reddit/search/comment/?before=1612066141&subreddit=stupidpol&size=100
200
https://api.pushshift.io/reddit/search/comment/?before=1612069200&subreddit=PokemonGoRaids&size=100
https://api.pushshift.io/reddit/search/comment/?before=1612068054&subreddit=PokemonGoRaids&size=100
200
https://api.pushshift.io/reddit/search/comment/?before=1612069200&subreddit=polls&size=100
https://api.pushshift.io/reddit/search/comment/?before=1612066214&subreddit=polls&size=100
200
https://api.pushshift.io/reddit/search/comment/?before=1612069200&subreddit=introvert&size=100
https://api.pushshift.io/reddit/search/comment/?before=1612031372&subreddit=introvert&size=100
200
https://api.pushshift.io/reddit/search/comment/?before=1612069200&subreddit=ClashOfClans&size=100
https://api.pushshift.io/reddit/search/comment/?before=1612060847&subreddit=ClashOfClans&size=100
200
https://api.pushshift.

In [ ]:
len(user_dict)

141691

In [ ]:
user_dict.values()

dict_values([1612068623, 1612069046, 1612069198, 1612041653, 1612069198, 1612069149, 1612068496, 1612069196, 1612067035, 1612066724, 1612069196, 1612069196, 1612038191, 1612069195, 1612063532, 1612069194, 1612069194, 1612069194, 1612069073, 1612069193, 1612069193, 1612069192, 1612069192, 1612069192, 1612068881, 1612068772, 1612069191, 1612068425, 1612069092, 1612069190, 1612069188, 1612069188, 1612069188, 1612068375, 1612068576, 1612069186, 1612069186, 1612068774, 1612068298, 1612068887, 1612051688, 1612068932, 1612069182, 1612069182, 1611950291, 1612068502, 1612069147, 1612066192, 1612069036, 1612068671, 1612069178, 1612069178, 1612068989, 1612069178, 1612069178, 1612069100, 1612069177, 1612068571, 1612049586, 1612069176, 1612066194, 1612069174, 1612065477, 1612069173, 1612068881, 1612069172, 1612069172, 1612069171, 1612069170, 1612069170, 1612045740, 1612069169, 1612068862, 1612069169, 1612068978, 1612068859, 1612068572, 1612069168, 1612067198, 1612069167, 1612069030, 1612069167, 161

In [ ]:
control_user_df = pd.DataFrame.from_dict(user_dict, orient='index', columns=['created_utc'])
control_user_df.reset_index(inplace=True)
control_user_df = control_user_df.rename(columns={'index':'user'})
control_user_df.head()

NameError: ignored

In [ ]:
cd drive/MyDrive/

/content/drive/MyDrive


In [ ]:
cd MentalHealthReddit/Data/

/content/drive/MyDrive/MentalHealthReddit/Data


In [ ]:
control_user_df.to_csv('control_user_df.csv')

In [ ]:
username_df = pd.read_csv('control_user_df.csv')
username_df.head()

Unnamed: 0             user  created_utc
0           0  Skurk-the-Grimm   1612068623
1           1          Voltiel   1612069046
2           2       MasterKlaw   1612069198
3           3    AdvocateSaint   1612041653
4           4      FroggiJoy87   1612069198

In [ ]:
control_username = username_df['user'].tolist()

In [ ]:
len(control_username)

141691

In [ ]:
adhd_df = pd.read_csv('adhd.csv')
anxiety_df = pd.read_csv('anxiety.csv')
bipolar_df = pd.read_csv('bipolar.csv')
bpd_df = pd.read_csv('bpd.csv')
dep_df = pd.read_csv('dep.csv')
ptsd_df = pd.read_csv('ptsd.csv')
ptsd_df.head()

Unnamed: 0  ...  subreddit
0           0  ...       ptsd
1           1  ...       ptsd
2           2  ...       ptsd
3           3  ...       ptsd
4           4  ...       ptsd

[5 rows x 13 columns]

In [ ]:
username_encoded.keys()

dict_keys(['cluelessin', 'CPTSD811', 'angelhippie', 'SquishKittyxoxo', 'jennylovesyoualot', 'Prudent_Passenger596', 'boschde3', 'KatIsMentalSmolGirl', 'Horty519', 'AJazzy69', 'christopherl572', 'blacksesamepaste', 'christineleon_', 'depressed_autistic', 'chaiteadaddy', 'aps_1357', 'kozmonautika', 'jacksonfromaz', 'vanillalinguine', 'Phoenix-Echo', 'Zestyclose_Put_6870', 'Striking-Mousse115', 'jnewland1207', 'B-Sober', 'roadtoerehwon', 'Lemonjuice_gal', 'AppropriateLevel1044', 'SNJ_nurse', 'bluesbutton', 'Badcons', 'L1tho', 'salsadip17', 'sauce-cat98', 'mmm_liv', 'Piscesthefishy', 'Forsaken-Conflict-11', 'Shhmeggles', 'J0N4RN', 'throwaway_39807', 'diminishingblackness', '_grizzlydog', 'Riddarn97', 'AlyciaCarpenter', 'adMFKINGhd', 'thrwaway7423', 'narcoleptic-monkey', 'catc658', 'cup_of_black_coffee', 'aatarn', 'AlternativeFacade', 'Shoddy-Election-7986', 'goldengaytimes', 'bluesun89', 'Romcom1398', 'morgansola', 'yodawastall', 'mollynevergiveup', 'breezybrie5', 'HazelKathleen', 'Suntanl

In [ ]:
control_username = [x for x in control_username if x not in list(username_encoded.keys())]
len(control_username)
#removed users who were in the experimental group 

141386

In [ ]:
len(username_encoded)

7994

In [ ]:
def codeMoreUsernames(names):
  #takes in new names to encode
  token_map = {name: i+7994 for i, name in enumerate(names)}
  return token_map


In [ ]:
controlnames_encoded = codeMoreUsernames(control_username)

In [ ]:
len(controlnames_encoded)

141386

In [ ]:
all_names = username_encoded 
all_names.update(controlnames_encoded)
len(all_names)

149380

In [ ]:
ls

adhd_coms.csv     anxiety_subs.csv  bpd.csv              dep_subs.csv
adhd.csv          bipolar_coms.csv  bpd_subs.csv         ptsd_coms.csv
adhd_subs.csv     bipolar.csv       control_user_df.csv  ptsd.csv
anxiety_coms.csv  bipolar_subs.csv  dep_coms.csv         ptsd_subs.csv
anxiety.csv       bpd_coms.csv      dep.csv


In [ ]:
all_names_df = pd.DataFrame.from_dict(all_names, orient='index', columns=['code'])
all_names_df.reset_index(inplace=True)
all_names_df = all_names_df.rename(columns={'index': 'user'})
all_names_df.head()

user  code
0         cluelessin     0
1           CPTSD811     1
2        angelhippie     2
3    SquishKittyxoxo     3
4  jennylovesyoualot     4

In [ ]:
all_names_df.to_csv('all_usernames_encoded.csv')

In [ ]:
username_df.head()

Unnamed: 0             user  created_utc
0           0  Skurk-the-Grimm   1612068623
1           1          Voltiel   1612069046
2           2       MasterKlaw   1612069198
3           3    AdvocateSaint   1612041653
4           4      FroggiJoy87   1612069198

In [ ]:
username_df.rename(columns = {'user': 'author'}, inplace = True)
username_df.head()

Unnamed: 0           author  created_utc
0           0  Skurk-the-Grimm   1612068623
1           1          Voltiel   1612069046
2           2       MasterKlaw   1612069198
3           3    AdvocateSaint   1612041653
4           4      FroggiJoy87   1612069198

## Get data from the identified control users
(continued in DataGathering2.ipynb)

In [ ]:
 def getControlCommentData(df):
   """
   Takes in a dataframe, gets comments for each user
   """
  comment_dict = {}
  for user, time in zip(df['author'], df['created_utc']):
    #username=getName(user)
    data = getOtherComments(user, time)
    for comment in data:
      if comment != 'NaN':
        collectCommentData(comment, comment_dict)
  return comment_dict


In [ ]:
def getControlSubmissionData(df):
  """
  Takes in a dataframe, gets submissoins for each user 
  """
  submission_dict = {}
  for user, time in zip(df['author'], df['created_utc']):
    data = getOtherSubmissions(user, time)
    for submission in data:
      if submission != 'NaN':
        #collectData(submission, submission_dict)
        collectOtherSubmissionData(submission, submission_dict)
  return submission_dict


In [ ]:
first_comments = getControlCommentData(username_df[0:1000])
type(first_comments)

https://api.pushshift.io/reddit/search/comment/?author=Skurk-the-Grimm&after=1612068623&size=100
https://api.pushshift.io/reddit/search/comment/?author=Voltiel&after=1612069046&size=100
https://api.pushshift.io/reddit/search/comment/?author=MasterKlaw&after=1612069198&size=100
https://api.pushshift.io/reddit/search/comment/?author=AdvocateSaint&after=1612041653&size=100
https://api.pushshift.io/reddit/search/comment/?author=FroggiJoy87&after=1612069198&size=100
https://api.pushshift.io/reddit/search/comment/?author=tequila-la&after=1612069149&size=100
https://api.pushshift.io/reddit/search/comment/?author=brownzilla99&after=1612068496&size=100
https://api.pushshift.io/reddit/search/comment/?author=ALoudMeow&after=1612069196&size=100
https://api.pushshift.io/reddit/search/comment/?author=PaladinMax&after=1612067035&size=100
https://api.pushshift.io/reddit/search/comment/?author=nomoreshoppingsprees&after=1612066724&size=100
https://api.pushshift.io/reddit/search/comment/?author=rylaia&a

dict